In [5]:
cd dsc180A

/Users/chensizhu/Desktop/dsc180a


In [6]:
ls

HAGO Play With New Friends_v3.7.5_apkpure.com/
all_smali_code/
apk/
apk_source/
data/
data-injection.ipynb
week3 lab.ipynb


In [4]:
cd apk/android/arch/core/a

[Errno 2] No such file or directory: 'android/arch/core/a'
/Users/chensizhu/Desktop


In [23]:
ls

a$1.smali  a$2.smali  a.smali    b.smali    c.smali


In [312]:
import re
from collections import defaultdict
import json
import os
from lxml import html
import requests
import xml.etree.ElementTree as ET
import gzip
from bs4 import BeautifulSoup
import io
from urllib.request import urlopen
import collections 

In [201]:
project_dir='/Users/chensizhu/Desktop/dsc180a/'

In [8]:
#dir "all_smali_code" stores various folders, each one representing a category of hundreds of apps
#each folder in one category directory will be named by the name of the app
basepath='/Users/chensizhu/Desktop/dsc180a/'
basedir=os.path.join(basepath, "smali")
basedir
if not os.path.exists(basedir):
    os.mkdir(basedir)

apkdir=os.path.join(basepath, 'apk')
if not os.path.exists(apkdir):
    os.mkdir(apkdir)

In [9]:
# parse sitemap and get url

sitemap=requests.get("https://apkpure.com/sitemap.xml")
tree = html.fromstring(sitemap.content)
url = tree.xpath('//loc/text()')


In [10]:
#parse each url and get the category for each app
#store the urls according to the catefores into a dictionary
from urllib.parse import urlparse

url_dict=defaultdict(list)
category_pattern='https://apkpure.com/sitemaps/^(default|topics|tag|group)(-\d+)?.xml.gz'
for i in url:
    path=urlparse(i).path
    category=re.match("/sitemaps/(\w+)(-\d+)?.xml.gz", path).group(1)
    if category not in url_dict:
        url_dict[category]=[i]
    else:
        url_dict[category].append(i)

   

In [150]:
url_dict

defaultdict(list,
            {'default': ['https://apkpure.com/sitemaps/default.xml.gz'],
             'topics': ['https://apkpure.com/sitemaps/topics.xml.gz'],
             'tag': ['https://apkpure.com/sitemaps/tag.xml.gz',
              'https://apkpure.com/sitemaps/tag-1.xml.gz',
              'https://apkpure.com/sitemaps/tag-2.xml.gz'],
             'group': ['https://apkpure.com/sitemaps/group.xml.gz',
              'https://apkpure.com/sitemaps/group-1.xml.gz',
              'https://apkpure.com/sitemaps/group-2.xml.gz',
              'https://apkpure.com/sitemaps/group-3.xml.gz',
              'https://apkpure.com/sitemaps/group-4.xml.gz',
              'https://apkpure.com/sitemaps/group-5.xml.gz',
              'https://apkpure.com/sitemaps/group-6.xml.gz',
              'https://apkpure.com/sitemaps/group-7.xml.gz',
              'https://apkpure.com/sitemaps/group-8.xml.gz',
              'https://apkpure.com/sitemaps/group-9.xml.gz',
              'https://apkpure.com/sit

In [87]:
#I need to append selected ulrs for each category in url_dict in to the function to get to website for downloading apk
url = 'https://apkpure.com/sitemaps/art_and_design-35.xml.gz'

def download_gzip_link(url):
    r = requests.get(url)
    with gzip.GzipFile(fileobj=io.BytesIO(r.content)) as f:
        result = f.read()
        soup = BeautifulSoup(result, 'xml')
        x_default=soup.find_all("xhtml:link", {"hreflang":  "x-default"})
        result=[x_default[index].get('href') for index in range(len(x_default)) if index%2==0]
        return result

a=download_gzip_link(url)
a

['https://apkpure.com/best-wallpapers-qhd-fhd-cute-backgrounds/loitp.zbestwallpapers',
 'https://apkpure.com/theme-for-sony-xperia-c-abstract-wallpaper/sony.xperia.c.xperia.z3plus.xa.xa1.z3.nokia6.vivov5.oppoa37.f3plus.galaxy.s8.j1.j2.theme.launcher16',
 'https://apkpure.com/goku-rose-wallpaper/com.zeinhd.GokuRoseWallpaper',
 'https://apkpure.com/image-modification-motor-matic/com.desnanistudio.imagemodificationmotormatic',
 'https://apkpure.com/design-home-ideas-2018/com.desnanistudio.designhomeideas2018',
 'https://apkpure.com/theme-for-sony-xperia-pro-dynamic-wallpaper/sony.xperia.pro.xperia.z3plus.xa.xa1.z3.nokia6.vivov5.oppoa37.f3plus.galaxy.s8.j1.j2.theme.launcher11',
 'https://apkpure.com/themes-for-xolo-x1000-motorcycle-wallpaper/xolo.xolo.x1000.era.era4g.era2x.era1x.black.a500s.era2.nokia6.vivov5.oppoa37.intex.theme.launcher',
 'https://apkpure.com/kite-design-ideas/com.pratama.idedesainlayanglayang',
 'https://apkpure.com/keroppic-hd-wallpaper/com.SolutionsDev.keroppiwallpape

In [121]:
#each app has two links starting with https://apkpure.com or https://m.apkpure.com
#I will only extract the download link from the https://apkpure.com website, whose index is even
# download link is under <div class='details'--> <div class='down-wrap' --> <div class='down' 
#input: index of link is even
def get_download_link(link):
    app_name=re.match('(https://apkpure.com/(.+))/', link).group(2)
    resp = requests.get(link)
    data = resp.content
    filtered = BeautifulSoup(data).find_all("a", class_="da", href=True)
    x=filtered[0]['href']
    download_link="https://apkpure.com{}".format(x)
    out=[app_name, download_link]
    return out
    
        
# https://apkpure.com/best-wallpapers-qhd-fhd-cute-backgrounds/loitp.zbestwallpapers/download?from=details
#'https://apkpure.com/theme-for-sony-xperia-c-abstract-wallpaper/sony.xperia.c.xperia.z3plus.
#xa.xa1.z3.nokia6.vivov5.oppoa37.f3plus.galaxy.s8.j1.j2.theme.launcher16/download?from=details'

In [219]:
out=get_download_link(a[0])
# https://apkpure.com/best-wallpapers-qhd-fhd-cute-backgrounds/loitp.zbestwallpapers/download?from=details
out[0]

'best-wallpapers-qhd-fhd-cute-backgrounds'

In [156]:
#inpur was result from function get_download_link
#out[0]=app_name
#out[1]=download_link
def get_apk_from_download_link(out):
    #direcory to store folders for each category
    cat_dir=''
    #directory to store apk files of all the app
    apk_dir='apk'
    current_dir=os.getcwd()
    out=get_download_link(x)
    app_name, download_link=out[0], out[1]
    file_dir='./'+cat_dir+'/'+apk_dir
    resp = requests.get(download_link)
    data = resp.content
    if not os.path.exists(file_dir):
        os.mkdir(file_dir)
    with open(file_dir+'/'+app_name+'.apk', 'wb') as fh:
        fh.write(data)
    

In [158]:
get_apk_from_download_link(out)

In [ ]:
### change apk t0 smali

In [218]:


%%bash
cd ./apk
for f in *.apk; do
  apktool d $f;
done
cd ..
    


Destination directory (/Users/chensizhu/Desktop/dsc180a/apk/design-home-ideas-2018) already exists. Use -f switch if you want to overwrite it.


In [323]:
#for every smali code, I extract all the lines within each blocks.
#appName: appName

def extract_features_for_app(app_smali_folder_dir):
    method_pattern='^.method'
    end_method_pattern='^.end\smethod'
    app_name_pattern='/Users/chensizhu/Desktop/dsc180a/apk/(.+)'
    new_line_pattern='[\r\n]'
    target_line_pattern='\s+invoke-'
    invoke_method_pattern='.+(invoke-(direct|static|virtual|super|interface)).+'
    package_pattern='.+(L.+(\$.)?);.+'
    API_call_pattern='.+(L.+(\$.)?;.+)\n$'

    app_name=re.match(app_name_pattern,app_smali_folder_dir).group(1)

    API_invoke_methods=defaultdict(list)
    API_package=defaultdict(list)
    app_API=defaultdict(list)
    API_codeblocks=[]

    add_line=False


    for dirpath, dirname, files in os.walk(app_smali_folder_dir):
        for file in files:
            if file.endswith('.smali'):
                with open(os.path.join(dirpath, file), 'r+') as auto:
                    with open(auto.name, 'r+') as f:

                        for i in f.readlines():
                            new_line=re.match(new_line_pattern, i)
                            start_method=re.match(method_pattern, i)
                            end_method=re.match(end_method_pattern, i)
                            target_line=re.match(target_line_pattern, i)

                            if new_line:
                                continue
                            if start_method:
                                add_line=True
                                API_single_codeblock=[]
                            if end_method:
                                add_line=False
                                API_codeblocks.append(API_single_codeblock)
                            if add_line==True:
                                #extract invoke method, API calls once the line is target line within the code clocks
                                if target_line:
                                    #extract invoke_method+package+API calls
                                    #method_type is among 'invoke-static', 'invoke-virtual', 
                                    #'invoke-direct', 'invoke-super', 'invoke-interface'
                                    invoke_method=re.match(invoke_method_pattern, i).group(1)
                                    #find the package after the invoke method
                                    #find the API call

                                    #find the package after the invoke method
                                    try:
                                        package=re.match(package_pattern, i).group(1)
                                        API_call=re.match(API_call_pattern, i).group(1)
                                    except:
                                        pass
                                    #### API-InvokeMethod
                                    if API_call not in API_invoke_methods[invoke_method]:
                                        API_invoke_methods[invoke_method].append(API_call)
                                    else:
                                        continue
                                    #### API-package
                                    if API_call not in API_package[package]:
                                        API_package[package].append(API_call)
                                    else:
                                        continue
                                    #### API_call in single code block
                                    if API_call not in API_single_codeblock:
                                        API_single_codeblock.append(API_call)
                                    else:
                                        continue
                                    #### app-API
                                    app_API[app_name].append(API_call)

    output=[API_package,API_invoke_methods,app_API,API_codeblocks]
    
    output=[API_package,API_invoke_methods,app_API,API_codeblocks]
    output_name=['API_package', 'API_invoke_methods', 'app_API', 'API_codeblocks']

    for i in range(len(output)):
        relationship_dir='smali/'+output_name[i]
        print(relationship_dir)
        if not os.path.exists(relationship_dir):
            os.mkdir(relationship_dir)
        data=output[i]
        with open(project_dir+'smali/'+output_name[i]+'/'+app_name+'.json', 'w+') as f:
            json.dump(data, f)
    return output
        


        
    




In [326]:
app_smali_folder_dir='/Users/chensizhu/Desktop/dsc180a/apk/Coin Dozer Free Prizes_v21.5_apkpure.com'
out_example=extract_features_for_app(app_smali_folder_dir)

smali/API_package
smali/API_invoke_methods
smali/app_API
smali/API_codeblocks


# Feature Extraction
### API Call Extraction
- trace over all the API calls and store them

## Relationship Analysis 
#### API-ClockBlock
- API calls together in the same method 
- store API calls in each method

#### API-Package
- store API calls in the same package

#### API-InvokeMethod
- store invoke method in each API call

- I need a list to store all the API calls
- identify each method block : 
- identify each package in method block 
- identify invoke methods
- store invoke methods for each API calls: dictionary
- store API calls in each pacakge: dictionary
- store API calls in each method block: dictionary



<font color=blue>
Part 1
</font>


With the growth of Android malwares which increase the severity of damages to smart phone users, it's necessary for all the platforms containing source codes of apps to make sure that the apps posted online are safe. Therefore, it's important to test the app and distinguish them from benign ware to malware. 


<font color=blue>1. Why is the data is appropriate to address the problem?</font>

This project is to use machine learning skills to distinguish the benign wares and malwares based on the features we extracted. In order to keep the data balanced and available, the data should consist of features from both benign wares and malwares. As for the type of the data, smali code is very appropriate here, because it can indicate the relationship between the app and API calls, which is the very important indicator for this project



<font color=blue>2. What are the potential shortcomings of the data for addressing the problem?</font>

I think is the simplicity of features. Using Smali Code can only indicate the relationship between app and API call, but it can't tell us more information.


<font color=blue>3. What data have been used to address this problem in the past? (Historical context)</font>

Android Fragmentation


<font color=blue>4. Summarize relevant details of the data generating process, describing the population that the data represents, whether that population is relevant to the question at hand, while addressing possible questions of data reliability</font>

. The first step of data generating process is to create two directory "smali" and "apk". Inside "smali", there are four directories representing "API_package", "API_codeblocks", "API_invoke_methods", "app_API" that each contains json files collecting relationships as the name of the directory indicated. 

. The second step is to script sitemap and unzip each url in to xml file. Also, in this step, I also categorize each url by the name of url indicated, like "art_and_design-69" and "auto_and_vehicles-22". In each xml, there are various links to source code of apps. In this way, I can easily categorize the app and balance the porprotion of apps from each category in the machin learning phase.

. The thir step is to get the download link of apk of each app and store *.apk file in the directory "apk".

. The fourth step is to, by apktool, convert each .apk files to a smali folder containing lots of smali code. 

. The fifth step is to loop through app's smali code folders, extract features for each app as four json files and store them under four folders under directory "smali"

. As for the data reliability, since the data I script from sitemap will be labeled as benign wares, but there is still some uncertainty toward the quality of the app. If the app is malware, this mislabel will destroy the accurary at the end.

In [ ]:
<font color=blue>Text</font>

Part 2

Describe the data ingestion process. This description should:

Specify from where the data originates, addressing legal issues pertaining to access.

Address any data privacy concerns and how your data pipeline handles them.

Lay out the schema and justify the decisions (what's the unit corresponding to an observation? What are the storage considerations?)

Address the applicability of the pipeline to similar data sources you might anticipate using (what might those be?).



<font color=blue>Part 2</font>

<font color=blue>1. Specify from where the data originates, addressing legal issues pertaining to access.</font>

. The first step of data generating process is to create two directory "smali" and "apk". Inside "smali", there are four directories representing "API_package", "API_codeblocks", "API_invoke_methods", "app_API" that each contains json files collecting relationships as the name of the directory indicated. 

. The second step is to script sitemap and unzip each url in to xml file. Also, in this step, I also categorize each url by the name of url indicated, like "art_and_design-69" and "auto_and_vehicles-22". In each xml, there are various links to source code of apps. In this way, I can easily categorize the app and balance the porprotion of apps from each category in the machin learning phase.

. The thir step is to get the download link of apk of each app and store *.apk file in the directory "apk".

. The fourth step is to, by apktool, convert each .apk files to a smali folder containing lots of smali code. 

. The fifth step is to loop through app's smali code folders, extract features for each app as four json files and store them under four folders under directory "smali"

<font color=blue>2. Address any data privacy concerns and how your data pipeline handles them.</font>

. for the problem addressing data privacy, I won't directly write down the actual name of the app, instead, I will use a hash table to assign the app with a number. It not only protects the information of the app, but also is less time-consuming to search for the app

<font color=blue>3. Lay out the schema and justify the decisions (what's the unit corresponding to an observation? What are the storage considerations?)</font>

In [317]:
os.listdir("/Users/chensizhu/Desktop/dsc180a/smali")

['app_API', '.DS_Store', 'API_package', 'API_invoke_methods', 'API_codeblocks']

In [327]:
print(out_example[0])

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [328]:
print(out_example[1])

defaultdict(<class 'list'>, {'invoke-direct': ['Ljava/lang/Object;-><init>()V', 'ListenerAdapter;-><init>()V', 'Lcom/facebook/ads/redexgen/X/1O;-><init>(DDDZ)V', 'Lcom/facebook/ads/redexgen/X/Fq;-><init>()V', 'List;-><init>()V', 'Ljava/util/HashMap;-><init>()V', 'Ljava/lang/Throwable;)V', 'Landroid/os/IBinder;)V', 'Landroid/os/Parcel;)V', 'Landroid/os/Parcel;)Lcom/facebook/ads/redexgen/X/6m;', 'Lcom/facebook/ads/redexgen/X/6l;->C(I)[Lcom/facebook/ads/redexgen/X/6m;', 'Landroid/view/animation/Animation;-><init>()V', 'Lcom/facebook/ads/redexgen/X/2O;)V', 'Lcom/facebook/ads/redexgen/X/6T;-><init>()V', 'Landroid/view/View;)V', 'Lcom/facebook/ads/redexgen/X/7X;)Z', 'Landroid/animation/ValueAnimator;-><init>()V', 'Lcom/facebook/ads/redexgen/X/7X;)V', 'Lcom/facebook/ads/redexgen/X/6Q;)V', 'List;)V', 'Lcom/facebook/ads/redexgen/X/7X;IIII)V', 'Landroid/view/ViewPropertyAnimator;)V', 'Landroid/content/Context;)V', 'Landroid/graphics/Path;-><init>()V', 'Landroid/graphics/RectF;-><init>()V', 'Lcom

In [329]:
print(out_example[2])

defaultdict(<class 'list'>, {'Coin Dozer Free Prizes_v21.5_apkpure.com': ['Ljava/lang/Object;-><init>()V', 'List;)Ljava/util/List;', 'Landroid/net/TrafficStats;->getTotalRxBytes()J', 'Lcom/facebook/ads/redexgen/X/D5;->I(J)Lcom/facebook/ads/redexgen/X/DI;', 'ListenerAdapter;-><init>()V', 'Landroid/view/View;->setTranslationX(F)V', 'Landroid/view/View;->setTranslationY(F)V', 'Listener;)Landroid/view/ViewPropertyAnimator;', 'Lcom/facebook/ads/redexgen/X/7X;)V', 'Ljava/lang/Object;)Z', 'Lcom/facebook/ads/redexgen/X/6U;->k()V', 'LS;Z)Z', 'Lcom/facebook/ads/redexgen/X/1O;-><init>(DDDZ)V', 'Lcom/facebook/ads/redexgen/X/HU;)Lcom/facebook/ads/redexgen/X/GH;', 'Lcom/facebook/ads/redexgen/X/HU;)Ljava/lang/String;', 'Lcom/facebook/ads/redexgen/X/HC;)Ljava/util/Map;', 'Ljava/util/Map;)V', 'Lcom/facebook/ads/redexgen/X/DW;)Lcom/facebook/ads/redexgen/X/DI;', 'Lcom/facebook/ads/redexgen/X/Am;)Landroid/content/pm/ApplicationInfo;', 'Lcom/facebook/ads/redexgen/X/Am;->G(I)Lcom/facebook/ads/redexgen/X/DI;

In [330]:
print(out_example[3])

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




<font color=blue>4. Address the applicability of the pipeline to similar data sources you might anticipate using (what might those be?)</font>

dataframe